In [3]:
import sqlite3
import pandas as pd
from datetime import datetime



### Here you the database file containing 1 day of 1min data
The name of the file contains the date.

In [4]:
mktdata_db_file = "/workspace/data/crypto_md/20240602.mktdata.ohlcv.db"

### Simple query that gets everything into DataFrame

In [5]:
db_conn = sqlite3.connect(mktdata_db_file)

df = pd.read_sql_query("select * from coinbase_ohlcv_1min", db_conn)
df

tstamp exchange_id instrument_id        open        high  \
0     1717286400000000000    COINBASE  PAIR-BTC-USD  67719.2900  67721.7300   
1     1717286460000000000    COINBASE  PAIR-BTC-USD  67714.1600  67717.3500   
2     1717286520000000000    COINBASE  PAIR-BTC-USD  67709.8800  67709.8800   
3     1717286580000000000    COINBASE  PAIR-BTC-USD  67692.3300  67713.0600   
4     1717286640000000000    COINBASE  PAIR-BTC-USD  67713.0600  67721.3300   
...                   ...         ...           ...         ...         ...   
5755  1717372500000000000    COINBASE  PAIR-XRP-USD      0.5135      0.5136   
5756  1717372560000000000    COINBASE  PAIR-XRP-USD      0.5135      0.5135   
5757  1717372620000000000    COINBASE  PAIR-XRP-USD      0.5134      0.5135   
5758  1717372680000000000    COINBASE  PAIR-XRP-USD      0.5133      0.5135   
5759  1717372740000000000    COINBASE  PAIR-XRP-USD      0.5135      0.5135   

             low       close        volume          vwap  
0     67708.1100  67719.9600      1.888240  67713.845756  
1     67707.6800  67709.8800      0.655358  67712.153017  
2     67689.7000  67691.3100      1.001506  67697.965852  
3     67691.2200  67713.0600      5.652547  67695.441479  
4     67710.7700  67715.0500      2.997525  67715.683416  
...          ...         ...           ...           ...  
5755      0.5134      0.5136   2505.022090      0.513596  
5756      0.5134      0.5134   5612.821763      0.513489  
5757      0.5133      0.5133   5503.452073      0.513377  
5758      0.5133      0.5134   3925.979599      0.513428  
5759      0.5133      0.5133  21244.669839      0.513309  

[5760 rows x 9 columns]

### Timestamp is not very convenient, so we can make it look nicer

In [15]:
df["timestamp"] = pd.to_datetime(df['tstamp'], unit='ns')
df.set_index("timestamp", inplace=True)
df

tstamp exchange_id instrument_id  \
timestamp                                                            
2024-06-02 00:00:00  1717286400000000000    COINBASE  PAIR-BTC-USD   
2024-06-02 00:01:00  1717286460000000000    COINBASE  PAIR-BTC-USD   
2024-06-02 00:02:00  1717286520000000000    COINBASE  PAIR-BTC-USD   
2024-06-02 00:03:00  1717286580000000000    COINBASE  PAIR-BTC-USD   
2024-06-02 00:04:00  1717286640000000000    COINBASE  PAIR-BTC-USD   
...                                  ...         ...           ...   
2024-06-02 23:55:00  1717372500000000000    COINBASE  PAIR-XRP-USD   
2024-06-02 23:56:00  1717372560000000000    COINBASE  PAIR-XRP-USD   
2024-06-02 23:57:00  1717372620000000000    COINBASE  PAIR-XRP-USD   
2024-06-02 23:58:00  1717372680000000000    COINBASE  PAIR-XRP-USD   
2024-06-02 23:59:00  1717372740000000000    COINBASE  PAIR-XRP-USD   

                           open        high         low       close  \
timestamp                                                             
2024-06-02 00:00:00  67719.2900  67721.7300  67708.1100  67719.9600   
2024-06-02 00:01:00  67714.1600  67717.3500  67707.6800  67709.8800   
2024-06-02 00:02:00  67709.8800  67709.8800  67689.7000  67691.3100   
2024-06-02 00:03:00  67692.3300  67713.0600  67691.2200  67713.0600   
2024-06-02 00:04:00  67713.0600  67721.3300  67710.7700  67715.0500   
...                         ...         ...         ...         ...   
2024-06-02 23:55:00      0.5135      0.5136      0.5134      0.5136   
2024-06-02 23:56:00      0.5135      0.5135      0.5134      0.5134   
2024-06-02 23:57:00      0.5134      0.5135      0.5133      0.5133   
2024-06-02 23:58:00      0.5133      0.5135      0.5133      0.5134   
2024-06-02 23:59:00      0.5135      0.5135      0.5133      0.5133   

                           volume          vwap  
timestamp                                        
2024-06-02 00:00:00      1.888240  67713.845756  
2024-06-02 00:01:00      0.655358  67712.153017  
2024-06-02 00:02:00      1.001506  67697.965852  
2024-06-02 00:03:00      5.652547  67695.441479  
2024-06-02 00:04:00      2.997525  67715.683416  
...                           ...           ...  
2024-06-02 23:55:00   2505.022090      0.513596  
2024-06-02 23:56:00   5612.821763      0.513489  
2024-06-02 23:57:00   5503.452073      0.513377  
2024-06-02 23:58:00   3925.979599      0.513428  
2024-06-02 23:59:00  21244.669839      0.513309  

[5760 rows x 9 columns]

### If you want individual instruments, you could create the function

In [28]:
def get_instrument_md(instrument_id: str) -> pd.DataFrame:
    query = f"select * from coinbase_ohlcv_1min where instrument_id = '{instrument_id}'"
    df = pd.read_sql_query(query, db_conn)
    df["timestamp"] = pd.to_datetime(df['tstamp'], unit='ns')
    df.set_index("timestamp", inplace=True)
    return df

btc_df = get_instrument_md(instrument_id="PAIR-BTC-USD")
eth_df = get_instrument_md(instrument_id="PAIR-ETH-USD")
xrp_df = get_instrument_md(instrument_id="PAIR-XRP-USD")

from IPython.display import display
display(btc_df)
display(eth_df)
display(xrp_df)



tstamp exchange_id instrument_id      open  \
timestamp                                                                      
2024-06-02 00:00:00  1717286400000000000    COINBASE  PAIR-BTC-USD  67719.29   
2024-06-02 00:01:00  1717286460000000000    COINBASE  PAIR-BTC-USD  67714.16   
2024-06-02 00:02:00  1717286520000000000    COINBASE  PAIR-BTC-USD  67709.88   
2024-06-02 00:03:00  1717286580000000000    COINBASE  PAIR-BTC-USD  67692.33   
2024-06-02 00:04:00  1717286640000000000    COINBASE  PAIR-BTC-USD  67713.06   
...                                  ...         ...           ...       ...   
2024-06-02 23:55:00  1717372500000000000    COINBASE  PAIR-BTC-USD  67757.09   
2024-06-02 23:56:00  1717372560000000000    COINBASE  PAIR-BTC-USD  67755.00   
2024-06-02 23:57:00  1717372620000000000    COINBASE  PAIR-BTC-USD  67755.39   
2024-06-02 23:58:00  1717372680000000000    COINBASE  PAIR-BTC-USD  67757.27   
2024-06-02 23:59:00  1717372740000000000    COINBASE  PAIR-BTC-USD  67752.14   

                         high       low     close    volume          vwap  
timestamp                                                                  
2024-06-02 00:00:00  67721.73  67708.11  67719.96  1.888240  67713.845756  
2024-06-02 00:01:00  67717.35  67707.68  67709.88  0.655358  67712.153017  
2024-06-02 00:02:00  67709.88  67689.70  67691.31  1.001506  67697.965852  
2024-06-02 00:03:00  67713.06  67691.22  67713.06  5.652547  67695.441479  
2024-06-02 00:04:00  67721.33  67710.77  67715.05  2.997525  67715.683416  
...                       ...       ...       ...       ...           ...  
2024-06-02 23:55:00  67757.26  67750.32  67753.93  0.326117  67753.207138  
2024-06-02 23:56:00  67761.34  67735.05  67755.35  1.259457  67744.858199  
2024-06-02 23:57:00  67759.88  67753.74  67757.49  0.429578  67757.147946  
2024-06-02 23:58:00  67759.90  67748.41  67750.71  0.683678  67756.292991  
2024-06-02 23:59:00  67754.50  67725.25  67735.52  0.530943  67747.261494  

[1440 rows x 9 columns]

tstamp exchange_id instrument_id     open  \
timestamp                                                                     
2024-06-02 00:00:00  1717286400000000000    COINBASE  PAIR-ETH-USD  3812.49   
2024-06-02 00:01:00  1717286460000000000    COINBASE  PAIR-ETH-USD  3812.88   
2024-06-02 00:02:00  1717286520000000000    COINBASE  PAIR-ETH-USD  3812.92   
2024-06-02 00:03:00  1717286580000000000    COINBASE  PAIR-ETH-USD  3812.16   
2024-06-02 00:04:00  1717286640000000000    COINBASE  PAIR-ETH-USD  3813.16   
...                                  ...         ...           ...      ...   
2024-06-02 23:55:00  1717372500000000000    COINBASE  PAIR-ETH-USD  3783.34   
2024-06-02 23:56:00  1717372560000000000    COINBASE  PAIR-ETH-USD  3783.57   
2024-06-02 23:57:00  1717372620000000000    COINBASE  PAIR-ETH-USD  3783.86   
2024-06-02 23:58:00  1717372680000000000    COINBASE  PAIR-ETH-USD  3782.23   
2024-06-02 23:59:00  1717372740000000000    COINBASE  PAIR-ETH-USD  3779.86   

                        high      low    close      volume         vwap  
timestamp                                                                
2024-06-02 00:00:00  3812.92  3812.48  3812.65  296.984283  3812.885799  
2024-06-02 00:01:00  3812.92  3812.66  3812.92   22.584759  3812.885708  
2024-06-02 00:02:00  3812.92  3812.17  3812.17   36.230701  3812.738323  
2024-06-02 00:03:00  3813.17  3812.14  3813.17   66.984405  3812.827731  
2024-06-02 00:04:00  3813.17  3813.13  3813.17   82.781325  3813.169087  
...                      ...      ...      ...         ...          ...  
2024-06-02 23:55:00  3784.43  3783.33  3783.57   17.409328  3783.902157  
2024-06-02 23:56:00  3783.86  3782.20  3783.86    6.632875  3783.094935  
2024-06-02 23:57:00  3783.94  3782.16  3782.18    7.826235  3782.958328  
2024-06-02 23:58:00  3782.24  3779.83  3779.86    9.020492  3781.022292  
2024-06-02 23:59:00  3780.05  3778.26  3778.88   39.588810  3778.964208  

[1440 rows x 9 columns]

tstamp exchange_id instrument_id    open  \
timestamp                                                                    
2024-06-02 00:00:00  1717286400000000000    COINBASE  PAIR-XRP-USD  0.5184   
2024-06-02 00:01:00  1717286460000000000    COINBASE  PAIR-XRP-USD  0.5180   
2024-06-02 00:02:00  1717286520000000000    COINBASE  PAIR-XRP-USD  0.5182   
2024-06-02 00:03:00  1717286580000000000    COINBASE  PAIR-XRP-USD  0.5181   
2024-06-02 00:04:00  1717286640000000000    COINBASE  PAIR-XRP-USD  0.5184   
...                                  ...         ...           ...     ...   
2024-06-02 23:55:00  1717372500000000000    COINBASE  PAIR-XRP-USD  0.5135   
2024-06-02 23:56:00  1717372560000000000    COINBASE  PAIR-XRP-USD  0.5135   
2024-06-02 23:57:00  1717372620000000000    COINBASE  PAIR-XRP-USD  0.5134   
2024-06-02 23:58:00  1717372680000000000    COINBASE  PAIR-XRP-USD  0.5133   
2024-06-02 23:59:00  1717372740000000000    COINBASE  PAIR-XRP-USD  0.5135   

                       high     low   close        volume      vwap  
timestamp                                                            
2024-06-02 00:00:00  0.5184  0.5180  0.5181  68137.158944  0.518082  
2024-06-02 00:01:00  0.5182  0.5179  0.5182   3659.609883  0.518028  
2024-06-02 00:02:00  0.5182  0.5179  0.5180   9693.379122  0.517920  
2024-06-02 00:03:00  0.5184  0.5180  0.5184   8324.107832  0.518215  
2024-06-02 00:04:00  0.5184  0.5183  0.5183   1482.065565  0.518348  
...                     ...     ...     ...           ...       ...  
2024-06-02 23:55:00  0.5136  0.5134  0.5136   2505.022090  0.513596  
2024-06-02 23:56:00  0.5135  0.5134  0.5134   5612.821763  0.513489  
2024-06-02 23:57:00  0.5135  0.5133  0.5133   5503.452073  0.513377  
2024-06-02 23:58:00  0.5135  0.5133  0.5134   3925.979599  0.513428  
2024-06-02 23:59:00  0.5135  0.5133  0.5133  21244.669839  0.513309  

[1440 rows x 9 columns]